In [1]:
# import packages used in this notebook
import os # need this to read the list of files in the directory
import io # need this to read the data from the zip file
from zipfile import ZipFile  # need this to read the data from the zip file
import tarfile # need this to read the data from the tar file
import json
import bz2
import gzip
import re # this is used for the regular expression to extract the subject from the file 

In [2]:
def loadtoMongo(contents, subject):
    from pymongo import MongoClient
    client = MongoClient('localhost', 27017)
    db = client['twitter']
    collection = db['tweets']
    subj = subject.lower()
    for line in contents:
        try:
            data = json.loads(line)
            # filter the data for my subject
            fltrData = re.search(r'\b{}\b'.format(subj), line.lower())

            if fltrData:
                try:
                    # if the subject is in the text, then load the entire line into mongo
                    content_dict = json.loads(line)
                    collection.insert_one(content_dict)
                except KeyError as e:
                    #print("KeyError encountered", {e}) # error is encountered mainly due to deleted tweets 
                    #print(line)
                    continue
        except json.decoder.JSONDecodeError as e:
            print("Error encountered at line: ", {e})
            continue
    
   

In [3]:
# tweetDrv = "/home/sba22230/shared-drives/E:/TwitterStream"
tweetDrv = "./SampleTweets/"
tweetWrappers = os.listdir(tweetDrv)
#display(tweetWrappers)


In [4]:
def bz2_func(data):
    data = bz2.decompress(data)
    data = io.StringIO(data.decode('utf-8'))
    contents = data.readlines()
    return contents

def gz_func(data):
    
    data = gzip.decompress(data)
    data = io.StringIO(data.decode('utf-8'))
    contents = data.readlines()
    return contents

for wrap in tweetWrappers:
    file = tweetDrv + wrap
    if file.endswith('.zip'):
        print("Zip file found") # need to a count of the files in the zip file format
        #display(file)
        with ZipFile(file, 'r') as zip:
            zipLn = len(zip.namelist())
            for i in range(zipLn):
                print(i, zip.namelist()[i])
                files = zip.namelist()[i]
                if files.endswith('bz2'):
                    data = zip.read(files)
                    contents = bz2_func(data) # now that we have the contents, we can push the tweets into mongoDB    
                    loadtoMongo(contents, 'euro')
                elif files.endswith('gz'):
                    data = zip.read(files)
                    contents = gz_func(data)
                    loadtoMongo(contents, 'euro')
                else:
                    print("unknown file" + os.path.splitext(files)[-1])
    elif file.endswith('.tar'):
        print("Tar file found") # need to a count of the files in the tar file format
        with tarfile.open(file, 'r') as tar:
            tarLn = len(tar.getnames())
            for i in range(tarLn):
                print(i, tar.getnames()[i])
                files = tar.getnames()[i]
                if files.endswith('bz2'):
                    data = tar.extractfile(files)
                    contents = bz2_func(data) # now that we have the contents, we can push the tweets into mongoDB    
                    loadtoMongo(contents, 'euro')
                elif files.endswith('gz'):
                    data = tar.extractfile(files)
                    contents = gz_func(data)
                    loadtoMongo(contents, 'euro')
    else:
        print("unknown file" + os.path.splitext(file)[-1])


unknown file.json
unknown file.txt
unknown file.json
unknown file.json


In [5]:
with open(tweetDrv + '29.json') as f:
    contents = f.readlines()

In [6]:
loadtoMongo(contents, 'brexit')

In [7]:
display(contents)

['{"created_at":"Thu Jul 01 06:29:00 +0000 2021","id":1410485572347387910,"id_str":"1410485572347387910","text":"overcome \\uadf9\\ubcf5\\ud558\\ub2e4, \\uc774\\uaca8\\ub0b4\\ub2e4\\noverlook \\uac04\\uacfc\\ud558\\ub2e4\\noverseas \\ud574\\uc678\\ub85c\\noverhead \\uba38\\ub9ac \\uc704\\uc5d0\\novertake \\ub530\\ub77c\\uc7a1\\ub2e4\\noverwhelm \\uc555\\ub3c4\\ud558\\ub2e4, \\ub2f9\\ud669\\ud558\\uac8c \\ud558\\ub2e4\\noverthrow \\uc804\\ubcf5\\uc2dc\\ud0a4\\ub2e4, \\ud3d0\\uc9c0\\ud558\\ub2e4\\noverwork \\uacfc\\ub85c\\ud558\\ub2e4","source":"\\u003ca href=\\"http:\\/\\/twittbot.net\\/\\" rel=\\"nofollow\\"\\u003etwittbot.net\\u003c\\/a\\u003e","truncated":false,"in_reply_to_status_id":null,"in_reply_to_status_id_str":null,"in_reply_to_user_id":null,"in_reply_to_user_id_str":null,"in_reply_to_screen_name":null,"user":{"id":950965398249197569,"id_str":"950965398249197569","name":"\\ub2e8\\uc5b4\\ubd07","screen_name":"Word__Origin","location":null,"url":null,"description":null,"translat

In [8]:
from pymongo import MongoClient
client = MongoClient('localhost', 27017)
db = client['twitter']
collection = db['tweets']

In [9]:
collection.insert_one(line)

NameError: name 'line' is not defined

In [ ]:
for line in contents:
    type(line)

In [ ]:
type(dict(line))